In [1]:
import plotly.express as px
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
import pandas as pd

import plotly.graph_objects as go
from plotly.subplots import make_subplots

In [38]:
def churn_rate_agg(x):
    return 1-x.mean()
import pycountry_convert as pc

def country_to_continent(country_name):
    country_alpha2 = pc.country_name_to_country_alpha2(country_name)
    try:
        country_continent_code = pc.country_alpha2_to_continent_code(country_alpha2)
        country_continent_name = pc.convert_continent_code_to_continent_name(country_continent_code)

    except KeyError as ke:
        #only SX not found 
        country_continent_name = 'North America'
        #print('continent not found ', country_alpha2)
    return country_continent_name


# Subscription Analysis 

The goal of the analysis is to determine the churn rate and why user are leaving or not. 


We first look at the subscription table which contain info for each user_id and for each subscription (There is one line per subscriptions (several line for one user) : 
  - subscription date
  - the number of inscription per users
  - if it is the first inscription or not, if the user come back or not after one churn year
  - if the user re-subscribe for the following year 
  - the user residential country 
  - if the user used promotion or payment3x 
  - if the user were referral
 

The dataset is from 2019-01-01 to 2022-11-30. As subscription are for one year, the maximal date subscription date is '2021-10-31'.

Some cleaning and selection were done in SQL BigQuery, using DBT


The next step in the notebook (HERE) will be to investigate the profile of churner according to their profile of user (if they are host or guest, if the made a lot of exchange or not etc..) 

## Loadind dataset 

Previously clean and stagged in SQL (DBT) 

In [37]:
df_subs = pd.read_hdf('data/subscription.h5', key='data')

len_=len(df_subs)

# DONE IN SQL
# #remove multiple inscription in same year while it's an annual subscription
# multiplesub = df_subs.groupby('user_id').agg({'pk':'count', 'renew':'mean'})
# print(len(multiplesub[multiplesub.pk>=4]))
# df_subs=df_subs[~df_subs.user_id.isin(multiplesub[multiplesub.pk>=4].index.values)]
# print(round(100-(len(df_subs)/len_)*100,1), ' % of double inscription for same user in the same year')


# remove user wihtout country 
df_subs = df_subs[df_subs.country.isnull()==False]
print('cleaning stage in SQL remove : ', round(100-len_/100000*100, 2) , '% of data')

# cast date
df_subs['first_subscription_date']= pd.to_datetime(df_subs['first_subscription_date'])
df_subs['subscription_date']= pd.to_datetime(df_subs['subscription_date'])
df_subs['previous_subscription_date']= pd.to_datetime(df_subs['previous_inscription_date'])

cleaning stage in SQL remove :  4.37 % of data


In [34]:
df_subs=df_subs.set_index('subscription_date')

In [39]:
# add continent info
df_subs['continent'] = df_subs["country"].apply(lambda x: country_to_continent(x))

In [41]:
total_churn = round((1-df_subs[['renew']].mean()[0])*100,2)
df_churn_tot = pd.DataFrame(dict({'status':['Churn','Renew'],'value':[total_churn,100-total_churn]}))
print('Total churn percentage ',total_churn , '%')
px.pie(data_frame=df_churn_tot,values='value', names='status',color_discrete_sequence=px.colors.sequential.Magma_r)


Total churn percentage  33.03 %


In [44]:
fig = go.Figure(data=go.Choropleth(
    locations = df_subs['country'],
    z = df_subs['renew'],
    text = df_subs['country'],
    colorscale = 'Inferno',
    autocolorscale=False,
    reversescale=True,
    marker_line_color='darkgray',
    marker_line_width=0.5,
    colorbar_title = 'Years',
))
fig.show()

In [ ]:
fig = px.bar(barmode='group', title ='')

fig.add_bar(x=df_subs.groupby('continent').agg({'user_id':  'count', 'renew':churn_rate_agg}).reset_index().continent,
            y=df_subs.groupby('continent').agg({'user_id':  'count', 'renew':churn_rate_agg}).reset_index().renew,name='total')
len(df_subs[df_subs.continent=='South America'])/len(df_subs)*100

In [ ]:
df_monthly  = df_subs.resample("2W").agg({'user_id': 'count', 'renew':'mean',
                                          'first_subscription':'mean',
                                                'is_zombie':'mean','promotion':'mean'})
df_monthly_northamerica = df_subs_northamerica.resample("2W").agg({'user_id': 'count', 'renew':'mean',
                                                                   'first_subscription':'mean',
                                                'is_zombie':'mean','promotion':'mean'})

df_monthly_europe = df_subs_europe.resample("2W").agg({'user_id': 'count', 'renew':'mean',
                                                       'first_subscription':'mean',
                                                'is_zombie':'mean','promotion':'mean'})

In [ ]:
df_monthly = df_monthly.rename(columns={"user_id": "subscription_count", 
                                        "renew": "churn_percentage", 
                                        "is_zombie":"return_percentage"})



df_monthly_northamerica = df_monthly_northamerica.rename(columns={"user_id": "subscription_count", 
                                        "renew": "churn_percentage", 
                                        "is_zombie":"return_percentage"})


df_monthly_europe = df_monthly_europe.rename(columns={"user_id": "subscription_count", 
                                        "renew": "churn_percentage", 
                                        "is_zombie":"return_percentage"})

In [ ]:
df_monthly

In [ ]:
fig = make_subplots()
# Create figure with secondary y-axis
#fig = make_subplots(specs=[[{"secondary_y": True}]])

# Add traces
fig.add_trace(
    go.Scatter(x=df_monthly.index, y=df_monthly.subscription_count, 
               name="Subscription Count",
               line = dict(color='firebrick', width=4, dash='dot')),
    secondary_y=False,
)


fig.add_trace(
    go.Scatter(x=df_monthly_northamerica.index, y=df_monthly_northamerica.subscription_count, 
               name="Subscription Count (NA)",
               line = dict(color='blue', width=4, dash='dot')),
    secondary_y=False,
)



fig.add_trace(
    go.Scatter(x=df_monthly_europe.index, y=df_monthly_europe.subscription_count, 
               name="Subscription Count (EU)",
               line = dict(color='green', width=4, dash='dot')),
    secondary_y=False,
)




# Set y-axes titles
fig.update_yaxes(title_text="#", secondary_y=False)
fig.update_yaxes(range=[0,3000], secondary_y=False)


# specify the corners of the rectangles
fig.update_layout(
    shapes=[
    dict(
        type="rect",
        xref="x",
        yref="y",
        x0="2020-03-01",
        y0="0",
        x1="2020-06-01",
        y1="5000",
        fillcolor="orange",
        opacity=0.4,
        line_width=0,
        layer="below", 
    ),
    dict(
        type="rect",
        xref="x",
        yref="y",
        x0="2020-11-01",
        y0="0",
        x1="2020-12-15",
        y1="5000",
        fillcolor="orange",
        opacity=0.4,
        line_width=0,
        layer="below", 
    )       
    ]
)



covid_label = f"<br>".join([f"Covid19",
                      f"Lookdown"])

fig.add_annotation(x="2020-04-15", y=3000,  showarrow=False,
                        text=covid_label
                )


fig.add_annotation(x="2020-11-15", y=3000,  showarrow=False,
                        text=covid_label
                )
fig.show()



fig = make_subplots()


fig.add_trace(
    go.Scatter(x=df_monthly.index+pd.offsets.DateOffset(years=1),
               y=(1-df_monthly.churn_percentage)*100 , name="Churn rate (%)"),
    secondary_y=False,
)


fig.add_trace(
    go.Scatter(x=df_monthly.index,
               y=(df_monthly.first_subscription)*100 , name="first inscription rate (%)"),
    secondary_y=False,
)


fig.add_trace(
    go.Scatter(x=df_monthly.index,
               y=(df_monthly.return_percentage)*100 , name="return rate (%)"),
    secondary_y=False,
)


fig.add_trace(
    go.Scatter(x=df_monthly_northamerica.index+pd.offsets.DateOffset(years=1),
               y=(1-df_monthly_northamerica.churn_percentage)*100 , name="Churn rate (%) (NA)"),
    secondary_y=False,
)


fig.add_trace(
    go.Scatter(x=df_monthly_europe.index+pd.offsets.DateOffset(years=1),
               y=(1-df_monthly_europe.churn_percentage)*100 , name="Churn rate (%) (EU)"),
    secondary_y=False,
)



fig.add_annotation(x="2021-07-01", y=total_churn+10,  showarrow=False,
                        text="Total Churn Rate",
                )



covid_label = f"<br>".join([f"Covid19",
                      f"Lookdown"])

# specify the corners of the rectangles
fig.update_layout(
    shapes=[
    dict(
        type="rect",
        xref="x",
        yref="y",
        x0="2020-03-01",
        y0="0",
        x1="2020-06-01",
        y1="5000",
        fillcolor="orange",
        opacity=0.4,
        line_width=0,
        layer="below", 
    ),
    dict(
        type="rect",
        xref="x",
        yref="y",
        x0="2020-11-01",
        y0="0",
        x1="2020-12-15",
        y1="5000",
        fillcolor="orange",
        opacity=0.4,
        line_width=0,
        layer="below", 
    )       
    ]
)

fig.add_annotation(x="2020-04-15", y=60,  showarrow=False,
                        text=covid_label
                )



fig.add_annotation(x="2020-11-15", y=60,  showarrow=False,
                        text=covid_label
                )


fig.update_yaxes(range=[0,100], secondary_y=False)
fig.add_hline(y=total_churn, )
fig.update_yaxes(title_text="%", secondary_y=False)


fig.show()



## Covid Analysis

Covid does have an impact on both inscription and churn rate, which decrease after Covid. Less churn after covid. Does the people that churn after covid are the same than before ? 

### Verify that Covid does impact Churn rate 
#### Hypothesis testing  on churn rate

In [ ]:
df_subs['covid_renew'] = np.where(df_subs.index +pd.offsets.DateOffset(years=1)>=pd.to_datetime('2021-04-15'), 
                            '1_post-covid','0_pre-covid')

tab = pd.crosstab(df_subs.covid_renew,df_subs.renew)
tab

In [ ]:
import scipy.stats as stats

# CONDUCT FISHER_EXACT STATISTICAL TEST
odds_ratio, p_value = stats.fisher_exact(tab)
# PRINT OUT RESULTS
if p_value < 0.05:
    print(f'p_value: {p_value}\nResult: There is a significant difference')
else:
    print(f'p_value: {p_value}\nResult: No significant difference')

In [ ]:
# chi2 
chiRes = stats.chi2_contingency(tab)
p_value = chiRes[1]
if p_value < 0.05:
    print(f'p_value: {p_value}\nResult: There is a significant difference')
else:
    print(f'p_value: {p_value}\nResult: No significant difference')

COVID had a impact on churn rate = less after covid but not on the number of inscription

### Is the case for inscription, first inscription

First Inscription

In [ ]:
df_subs['covid_subs'] = np.where(df_subs.index >=pd.to_datetime('2021-04-15'), 
                            '1_post-covid','0_pre-covid')

tab = pd.crosstab(df_subs.covid_subs,df_subs.first_subscription)
tab


In [ ]:
#tab = pd.crosstab(df_subs.covid, df_subs.first_subscription)
#tab
# CONDUCT FISHER_EXACT STATISTICAL TEST
odds_ratio, p_value = stats.fisher_exact(tab)
# PRINT OUT RESULTS
if p_value < 0.05:
    print(f'p_value: {p_value}\nResult: There is a significant difference')
else:
    print(f'p_value: {p_value}\nResult: No significant difference')

In [ ]:
# chi2 
chiRes = stats.chi2_contingency(tab)
p_value = chiRes[1]
if p_value < 0.05:
    print(f'p_value: {p_value}\nResult: There is a significant difference')
else:
    print(f'p_value: {p_value}\nResult: No significant difference')

Inscription  => Z test ? 

In [ ]:
df_count_inscription  = df_subs.resample("D").agg({'user_id': 'count'})

In [ ]:
df_post_covid = df_count_inscription[df_count_inscription.index >=pd.to_datetime('2021-04-15')]
df_pre_covid = df_count_inscription[df_count_inscription.index <pd.to_datetime('2021-04-15')]


In [ ]:
from statsmodels.stats.weightstats import ztest
zScore, pValue = ztest(df_pre_covid['user_id'], df_post_covid['user_id'])

In [ ]:
if p_value < 0.05:
    print(f'p_value: {p_value}\nResult: There is a significant difference')
else:
    print(f'p_value: {p_value}\nResult: No significant difference')

# Churn analysis


In [ ]:
df_subs_post_covid = df_subs[df_subs.covid_renew=='1_post-covid']
df_subs_pre_covid = df_subs[df_subs.covid_renew!='1_post-covid']

In [ ]:
fig = px.bar(barmode='group')

fig.add_bar(x=df_subs.groupby('continent').agg({'user_id':  'count', 'renew':'mean'}).reset_index().continent,
            y=df_subs.groupby('continent').agg({'user_id':  'count', 'renew':'mean'}).reset_index().renew,name='total')
fig.add_bar(x=df_subs_post_covid.groupby('continent').agg({'user_id':  'count', 'renew':'mean'}).reset_index().continent,
             y=df_subs_post_covid.groupby('continent').agg({'user_id':  'count', 'renew':'mean'}).reset_index().renew,
            name='post-covid')
fig.add_bar(x=df_subs_pre_covid.groupby('continent').agg({'user_id':  'count', 'renew':'mean'}).reset_index().continent,
             y=df_subs_pre_covid.groupby('continent').agg({'user_id':  'count', 'renew':'mean'}).reset_index().renew, 
           name='pre-covid')


### Nb inscription 

In [ ]:
fig = px.bar(barmode='group')
fig.add_bar(x=df_subs.groupby('first_subscription').agg({'user_id':  'count', 'renew':'mean'}).reset_index().first_subscription,
       y=df_subs.groupby('first_subscription').agg({'user_id':  'count', 'renew':'mean'}).reset_index().renew,name='total')
fig.add_bar(x=df_subs_post_covid.groupby('first_subscription').agg({'user_id':  'count', 'renew':'mean'}).reset_index().first_subscription,
             y=df_subs_post_covid.groupby('first_subscription').agg({'user_id':  'count', 'renew':'mean'}).reset_index().renew,
           name='post-covid')
fig.add_bar(x=df_subs_pre_covid.groupby('first_subscription').agg({'user_id':  'count', 'renew':'mean'}).reset_index().first_subscription,
             y=df_subs_pre_covid.groupby('first_subscription').agg({'user_id':  'count', 'renew':'mean'}).reset_index().renew,
           name='pre-covid')
            

In [ ]:

test= df_subs.groupby('user_id').agg({'pk':'count', 'renew':'mean'})
fig = px.bar(barmode='group')
fig.add_bar(x=test.groupby('pk').agg({'renew':'mean'}).reset_index().pk,
          y=test.groupby('pk').agg({'renew':'mean'}).reset_index().renew,name='total')
# fig.add_bar(x=df_subs_post_covid.groupby('first_subscription').agg({'user_id':  'count', 'renew':'mean'}).reset_index().first_subscription,
#              y=df_subs_post_covid.groupby('first_subscription').agg({'user_id':  'count', 'renew':'mean'}).reset_index().renew,
#            name='post-covid')
# fig.add_bar(x=df_subs_pre_covid.groupby('first_subscription').agg({'user_id':  'count', 'renew':'mean'}).reset_index().first_subscription,
#              y=df_subs_pre_covid.groupby('first_subscription').agg({'user_id':  'count', 'renew':'mean'}).reset_index().renew,
#            name='pre-covid')
            

In [ ]:
df_subs.head()

In [ ]:
TABLE par USER ID 